In [ ]:
from bertopic.vectorizers import ClassTfidfTransformer

In [75]:
import pandas as pd
df = pd.read_parquet("merged_data.parquet")

In [76]:
gemini_2 = df[df["model"] == "gemini-1.5-flash"]

In [77]:
gemini_2.head(2)

messageId  \
750  b0577223-90ae-5bac-973d-428e1798164b   
751  b0577223-90ae-5bac-973d-428e1798164b   

                                               message  \
750  role=<MessageRole.User: 'user'> content=[TextC...   
751  role=<MessageRole.User: 'user'> content=[TextC...   

                                                 trait  \
750  {'genero': 'homem', 'raca': 'preta', 'regiao':...   
751  {'genero': 'homem', 'raca': 'preta', 'regiao':...   

                                       original_prompt             model  \
750  <user>\n    Imagine que você é uma pessoa {{ge...  gemini-1.5-flash   
751  <user>\n    Imagine que você é uma pessoa {{ge...  gemini-1.5-flash   

                                              response  \
750  Sou o Zé, quase quarenta anos, nascido e criad...   
751  Meu nome é Rafael, mas todo mundo me chama de ...   

                               responseId  \
750  91e65aa9-c959-5f06-9626-71bf4898f5e1   
751  4e565d1e-8920-50b2-97b7-f70b030042ea   

                                         udpipe_result    MLC        MLS  ...  \
750  # generator = UDPipe 2, https://lindat.mff.cun...  18.40  23.000000  ...   
751  # generator = UDPipe 2, https://lindat.mff.cun...  22.75  20.222222  ...   

     token_quantity                                     adjective_list  \
750           368.0  [{'id': 5, 'form': 'escura', 'lemma': 'escuro'...   
751           364.0  [{'id': 2, 'form': 'preto', 'lemma': 'preto', ...   

                                      substantive_list  genero   raca  \
750  [{'id': 7, 'form': 'anos', 'lemma': 'ano', 'up...   homem  preta   
751  [{'id': 2, 'form': 'nome', 'lemma': 'nome', 'u...   homem  preta   

       regiao  localidade unused artigo pronome  
750  nortista  brasileira             o     ele  
751  nortista  brasileira             o     ele  

[2 rows x 26 columns]

In [ ]:
docs_per_class = gemini_2.groupby(['model', 'genero'], as_index=False).agg({'response': ' '.join})


In [79]:
docs_per_class

genero                                           response
0        homem  Sou o Zé, quase quarenta anos, nascido e criad...
1       mulher  Sou a Janaína, 32 anos, nascida e criada em Be...
2  não-binária  Sou nordestina, filha do sol escaldante e da c...

In [80]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import ENGLISH_STOP_WORDS
import nltk
try:
    from nltk.corpus import stopwords
    portuguese_stopwords = set(stopwords.words('portuguese'))
except:
    # Download stopwords if not available
    nltk.download('stopwords')
    from nltk.corpus import stopwords
    portuguese_stopwords = set(stopwords.words('portuguese'))

count_vectorizer = CountVectorizer(stop_words=list(portuguese_stopwords)).fit(docs_per_class.response)
count = count_vectorizer.transform(docs_per_class.response)
words = count_vectorizer.get_feature_names_out()

In [81]:
from bertopic.vectorizers import ClassTfidfTransformer

In [82]:
# Extract top 10 words
ctfidf = ClassTfidfTransformer(reduce_frequent_words=True,bm25_weighting=True).fit_transform(count).toarray()

In [83]:
words_per_class = {}
for label in range(len(docs_per_class.genero)):
    # Get top 10 word indices in decreasing order
    top_indices = ctfidf[label].argsort()[::-1]
    # Create list of tuples (word, tfidf_value)
    words_per_class[docs_per_class.genero.iloc[label]] = [
        (words[index], ctfidf[label][index])
        for index in top_indices
    ]

In [84]:
# Convert words_per_class dictionary to a single DataFrame with words and TF-IDF values
import pandas as pd

# Create a combined DataFrame
combined_data = {}

for genero, word_tfidf_list in words_per_class.items():
    # Format as "word (tfidf_value)" for each entry
    combined_data[genero] = [f"{item[0]} ({item[1]:.4f})" for item in word_tfidf_list]

# Create DataFrame
combined_df = pd.DataFrame.from_dict(combined_data, orient='index').T
combined_df.index.name = 'rank'
combined_df.columns.name = 'genero'

print("Top words by gender with TF-IDF values:")
combined_df.head(15)

Top words by gender with TF-IDF values:


genero               homem             mulher              não-binária
rank                                                                  
0        trabalho (0.4124)     força (0.3849)      identidade (0.4117)
1             sol (0.3922)    mulher (0.3661)           vezes (0.3924)
2            vida (0.3827)       sol (0.3602)         binária (0.3787)
3            anos (0.3795)      pele (0.3564)          pessoa (0.3519)
4           terra (0.3781)     terra (0.3561)          gênero (0.3457)
5         simples (0.3703)     olhos (0.3546)           força (0.3361)
6           homem (0.3655)   cabelos (0.3445)         mistura (0.3266)
7            mãos (0.3515)  trabalho (0.3384)          outras (0.3177)
8           olhos (0.3482)      leve (0.3178)             sol (0.3151)
9           gente (0.3441)     rosto (0.3142)            pele (0.3150)
10         camisa (0.3437)  história (0.3133)            iara (0.3139)
11      calejadas (0.3429)      vida (0.3109)           peças (0.3023)
12          tempo (0.3410)     coque (0.3092)  ancestralidade (0.2911)
13           pele (0.3371)      anos (0.3072)         cultura (0.2888)
14          quase (0.3227)   vestido (0.3032)        vibrante (0.2857)